In [1]:
import numpy as np
from datetime import datetime

from strat import MacdCrossAndRSIOver

from quantfreedom.enums import *
from quantfreedom.helper_funcs import dl_ex_candles
from quantfreedom.simulate import run_df_backtest, or_backtest


np.set_printoptions(formatter={"float_kind": "{:0.2f}".format})

%load_ext autoreload
%autoreload 2

In [2]:
candles = dl_ex_candles(
    exchange="mufex",
    symbol="ETHUSDT",
    timeframe="5m",
    candles_to_dl=10000,
    # since_datetime=datetime(2023, 1, 1),
    # until_datetime=datetime(2024, 2, 29),
)

In [3]:
# long_strat = MacdCrossAndRSIOver(
#     long_short="long",
#     rsi_length=np.array([14]),
#     rsi_is_below=np.arange(35, 61, 5),
#     ema_length=np.arange(200, 401, 200),
#     fast_length=np.arange(10, 21, 10),
#     macd_below=np.array([0]),    
#     signal_smoothing=np.arange(5, 16, 10),
#     slow_length=np.arange(30, 61, 30),
# )

long_strat = MacdCrossAndRSIOver(
    long_short="long",
    rsi_length=np.array([14]),
    rsi_is_below=np.arange(20, 46, 5),
    ema_length=np.arange(200, 401, 200),
    fast_length=np.arange(10, 21, 10),
    macd_below=np.array([0]),    
    signal_smoothing=np.arange(5, 16, 10),
    slow_length=np.arange(30, 61, 30),
)

# long_strat = MacdCrossAndRSIOver(
#     long_short="long",
#     rsi_length=np.array([14]),
#     rsi_is_below=np.arange(30, 61, 5),
#     ema_length=np.arange(200, 401, 200),
#     fast_length=np.array([12]),
#     macd_below=np.array([0]),    
#     signal_smoothing=np.array([9]),
#     slow_length=np.array([26]),
# )

# long_strat = MacdCrossAndRSIOver(
#     long_short="long",
#     rsi_length=np.array([14]),
#     rsi_is_below=np.array([30]),
#     ema_length=np.array([200]),
#     fast_length=np.array([12]),
#     macd_below=np.array([0]),    
#     signal_smoothing=np.array([9]),
#     slow_length=np.array([26]),
# )


long_strat.set_entries_exits_array(
    candles=candles,
    ind_set_index=0,
)
# long_strat.plot_signals(candles=candles)

bf 8
aft 8


In [4]:
backtest_settings = BacktestSettings()

exchange_settings = ExchangeSettings(
    asset_tick_step=3,
    leverage_mode=1,
    leverage_tick_step=2,
    limit_fee_pct=0.0003,
    market_fee_pct=0.0006,
    max_asset_size=100.0,
    max_leverage=150.0,
    min_asset_size=0.001,
    min_leverage=1.0,
    mmr_pct=0.004,
    position_mode=3,
    price_tick_step=1,
)


#test live
static_os = StaticOrderSettings(
    increase_position_type=IncreasePositionType.RiskPctAccountEntrySize,
    leverage_strategy_type=LeverageStrategyType.Dynamic,
    pg_min_max_sl_bcb="min",
    sl_strategy_type=StopLossStrategyType.SLBasedOnCandleBody,
    sl_to_be_bool=False,
    starting_bar=50,
    starting_equity=1000.0,
    static_leverage=None,
    tp_fee_type="market",
    tp_strategy_type=TakeProfitStrategyType.RiskReward,
    trail_sl_bool=True,
    z_or_e_type=None,
)



#qf_score 0.757 ind = 53, dos_index = 0 
# dos_arrays = DynamicOrderSettingsArrays(
#     max_equity_risk_pct=np.array([12]),
#     max_trades=np.array([5]),
#     risk_account_pct_size=np.array([3]),
#     risk_reward=np.array([3]),
#     sl_based_on_add_pct=np.array([0.25]),
#     sl_based_on_lookback=np.array([50]),
#     sl_bcb_type=np.array([CandleBodyType.Low]),
#     sl_to_be_cb_type=np.array([CandleBodyType.Nothing]),
#     sl_to_be_when_pct=np.array([0]),
#     trail_sl_bcb_type=np.array([CandleBodyType.Low]),
#     trail_sl_by_pct=np.array([0.5]),
#     trail_sl_when_pct=np.array([1]),
# )

# qf_score 0.817 idn = 21, doc_index = 0
dos_arrays = DynamicOrderSettingsArrays(
    max_equity_risk_pct=np.array([12]),
    max_trades=np.array([3]),
    risk_account_pct_size=np.array([3]),
    risk_reward=np.array([2]),
    sl_based_on_add_pct=np.array([1]),
    sl_based_on_lookback=np.array([30]),
    sl_bcb_type=np.array([CandleBodyType.Low]),
    sl_to_be_cb_type=np.array([CandleBodyType.Nothing]),
    sl_to_be_when_pct=np.array([0]),
    trail_sl_bcb_type=np.array([CandleBodyType.Low]),
    trail_sl_by_pct=np.array([1]),
    trail_sl_when_pct=np.array([1]),
)

In [5]:
backtest_results = run_df_backtest(
    backtest_settings=backtest_settings,
    candles=candles,
    dos_arrays=dos_arrays,
    exchange_settings=exchange_settings,
    static_os=static_os,
    strategy=long_strat,
)


Starting the backtest now ... and also here are some stats for your backtest.

Total indicator settings to test: 96
Total order settings to test: 1
Total combinations of settings to test: 96
Total candles: 10,000
Total candles to test: 960,000


In [6]:
backtest_results.sort_values(by=["qf_score","total_pnl"], ascending=False).head(10)
# backtest_results.sort_values(by=["ind_set_idx"], ascending=True).head(25)

ind_set_idx  dos_index  total_trades  wins  losses  gains_pct  win_rate  \
18           22          0           2.0     2       0      7.965   100.000   
26           30          0           2.0     2       0      7.965   100.000   
63           67          0          30.0    19      11     39.997    63.333   
71           75          0          30.0    19      11     39.997    63.333   
78           82          0          39.0    23      16     41.175    58.974   
86           90          0          39.0    23      16     41.175    58.974   
66           70          0          26.0    16      10     43.844    61.538   
74           78          0          26.0    16      10     43.844    61.538   
1             1          0           3.0     2       1      3.838    66.667   
3             4          0           3.0     2       1      3.838    66.667   

    qf_score  fees_paid  ending_eq  total_pnl  
18     1.000      3.590   1079.653     79.653  
26     1.000      3.590   1079.653     79.653  
63     0.753     97.316   1399.967    399.967  
71     0.753     97.316   1399.967    399.967  
78     0.699    234.540   1411.753    411.753  
86     0.699    234.540   1411.753    411.753  
66     0.696     96.841   1438.443    438.443  
74     0.696     96.841   1438.443    438.443  
1      0.617      4.531   1038.384     38.384  
3      0.617      4.531   1038.384     38.384

In [97]:
order_records_df = or_backtest(
    backtest_settings=backtest_settings,
    candles=candles,
    dos_arrays=dos_arrays,
    exchange_settings=exchange_settings,
    static_os=static_os,
    strategy=long_strat,
    dos_index=0,
    ind_set_index=65,
    plot_results=True,
    logger_bool=True,
)

DynamicOrderSettings(
    max_equity_risk_pct = 0.12,
    max_trades = 3,
    risk_account_pct_size = 0.02,
    risk_reward = 2.0,
    sl_based_on_add_pct = 0.01,
    sl_based_on_lookback = 30,
    sl_bcb_type = 3,
    sl_to_be_cb_type = 6,
    sl_to_be_when_pct = 0.0,
    trail_sl_bcb_type = 3,
    trail_sl_by_pct = 0.01,
    trail_sl_when_pct = 0.01,
)
IndicatorSettingsArrays(
    rsi_is_above = nan,
    rsi_is_below = 40.0,
    rsi_length = 14,
    ema_length = 200,
    fast_length = 10,
    macd_below = 0,
    signal_smoothing = 5,
    slow_length = 60,
)


d:\Lab\quantFreedom\qfstrat\lib\site-packages\_plotly_utils\basevalidators.py:105: FutureWarning:

The behavior of DatetimeProperties.to_pydatetime is deprecated, in a future version this will return a Series containing python datetime objects instead of an ndarray. To retain the old behavior, call `np.array` on the result

